In [5]:
import pandas as pd
import numpy as np
from collections import defaultdict

def assign_job_categories(job_names):
    categories = ['short', 'medium', 'long', 'very_long']
    probabilities = [0.7, 0.25, 0.04, 0.01]
    return {job: np.random.choice(categories, p=probabilities) for job in job_names}

def assign_upgrade_impact(job_names):
    impacts = ['improved', 'regressed', 'unchanged']
    probabilities = [0.5, 0.2, 0.3]
    return {job: np.random.choice(impacts, p=probabilities) for job in job_names}

def assign_schedule(job_names):
    schedules = ['15min', 'daily', 'monthly', 'unscheduled']
    probabilities = [0.6, 0.2, 0.05, 0.15]
    return {job: np.random.choice(schedules, p=probabilities) for job in job_names}

def generate_duration(category, is_after_upgrade, impact, schedule):
    base_duration = {
        'short': (1, 120),
        'medium': (120, 900),  # Changed upper limit to 15 minutes
        'long': (900, 86400),
        'very_long': (86400, 259200)
    }[category]
    
    if schedule == '15min':
        max_duration = 900  # 15 minutes in seconds
    elif schedule == 'daily':
        max_duration = 86400  # 1 day in seconds
    elif schedule == 'monthly':
        max_duration = 259200  # 3 days in seconds
    else:  # unscheduled
        max_duration = 259200  # 3 days in seconds

    duration = min(np.random.randint(*base_duration), max_duration)
    
    if is_after_upgrade:
        if impact == 'improved':
            duration = int(duration * np.random.uniform(0.5, 0.9))
        elif impact == 'regressed':
            duration = int(duration * np.random.uniform(1.1, 1.5))
    
    return max(1, min(duration, max_duration))

n_samples = 1000000
job_names = [f'JOB_{i}' for i in range(1, 167)]
job_categories = assign_job_categories(job_names)
job_impacts = assign_upgrade_impact(job_names)
job_schedules = assign_schedule(job_names)

data = defaultdict(list)

start_date = pd.Timestamp('2023-09-01')
upgrade_date = pd.Timestamp('2024-05-19')
end_date = pd.Timestamp('2024-06-22')

total_days = (end_date - start_date).days
pre_upgrade_days = (upgrade_date - start_date).days
post_upgrade_days = (end_date - upgrade_date).days

n_samples_pre = int(n_samples * (pre_upgrade_days / total_days))
n_samples_post = n_samples - n_samples_pre

oprids = ['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams', 'scheduler']

for is_after_upgrade, n in [(False, n_samples_pre), (True, n_samples_post)]:
    for _ in range(n):
        job_name = np.random.choice(job_names)
        job_category = job_categories[job_name]
        job_impact = job_impacts[job_name]
        job_schedule = job_schedules[job_name]
        
        if is_after_upgrade:
            request_date = upgrade_date + pd.Timedelta(seconds=np.random.randint(0, post_upgrade_days * 86400))
        else:
            request_date = start_date + pd.Timedelta(seconds=np.random.randint(0, pre_upgrade_days * 86400))
        
        oprid = np.random.choice(oprids)
        
        if oprid == 'scheduler':
            if job_schedule == '15min':
                request_date = request_date.floor('15min')
            elif job_schedule == 'daily':
                request_date = request_date.floor('D')
            elif job_schedule == 'monthly':
                request_date = request_date.floor('D').replace(day=1)
        
        duration = generate_duration(job_category, is_after_upgrade, job_impact, job_schedule)
        
        # Generate begin time after request time
        begin_delay = np.random.randint(1, 300)  # 1 to 300 seconds delay
        begin_time = request_date + pd.Timedelta(seconds=begin_delay)
        
        # Generate end time after begin time
        end_time = begin_time + pd.Timedelta(seconds=duration)
        
        data['RQSTDTTM'].append(request_date)
        data['PRCSNAME'].append(job_name)
        data['SECONDS'].append(duration)
        data['MINUTES'].append(duration // 60)
        data['RUNSTATUSDESC'].append(np.random.choice(['Success', 'Error'], p=[0.9, 0.1]))
        data['PRCSINSTANCE'].append(np.random.randint(100000, 999999))
        data['OPRID'].append(oprid)
        data['RUNCNTLID'].append(np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS']))
        data['IS_AFTER_UPGRADE'].append(is_after_upgrade)
        data['SCHEDULE'].append(job_schedule)
        data['BEGINDTTM'].append(begin_time)
        data['ENDDTTM'].append(end_time)

df = pd.DataFrame(data)

# Calculate actual duration based on BEGINDTTM and ENDDTTM
df['ACTUAL_DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60

# Display overall statistics
print(df['ACTUAL_DURATION'].describe())

# Display job counts before and after upgrade
print(f"\nTotal jobs: {len(df)}")
print(f"Jobs before upgrade: {len(df[~df['IS_AFTER_UPGRADE']])} ({len(df[~df['IS_AFTER_UPGRADE']]) / len(df) * 100:.2f}%)")
print(f"Jobs after upgrade: {len(df[df['IS_AFTER_UPGRADE']])} ({len(df[df['IS_AFTER_UPGRADE']]) / len(df) * 100:.2f}%)")

# Display job duration distribution for scheduler and non-scheduler jobs
for oprid_type in ['scheduler', 'non-scheduler']:
    subset = df[df['OPRID'] == 'scheduler'] if oprid_type == 'scheduler' else df[df['OPRID'] != 'scheduler']
    print(f"\nJob duration distribution for {oprid_type} jobs:")
    print(f"Under 2 minutes: {(subset['ACTUAL_DURATION'] < 2).sum()} ({(subset['ACTUAL_DURATION'] < 2).sum() / len(subset) * 100:.2f}%)")
    print(f"2 to 15 minutes: {((subset['ACTUAL_DURATION'] >= 2) & (subset['ACTUAL_DURATION'] < 15)).sum()} ({((subset['ACTUAL_DURATION'] >= 2) & (subset['ACTUAL_DURATION'] < 15)).sum() / len(subset) * 100:.2f}%)")
    print(f"15 minutes to 4 hours: {((subset['ACTUAL_DURATION'] >= 15) & (subset['ACTUAL_DURATION'] < 240)).sum()} ({((subset['ACTUAL_DURATION'] >= 15) & (subset['ACTUAL_DURATION'] < 240)).sum() / len(subset) * 100:.2f}%)")
    print(f"4 hours to 1 day: {((subset['ACTUAL_DURATION'] >= 240) & (subset['ACTUAL_DURATION'] < 1440)).sum()} ({((subset['ACTUAL_DURATION'] >= 240) & (subset['ACTUAL_DURATION'] < 1440)).sum() / len(subset) * 100:.2f}%)")
    print(f"1 day to 3 days: {((subset['ACTUAL_DURATION'] >= 1440) & (subset['ACTUAL_DURATION'] <= 4320)).sum()} ({((subset['ACTUAL_DURATION'] >= 1440) & (subset['ACTUAL_DURATION'] <= 4320)).sum() / len(subset) * 100:.2f}%)")

# Display average duration for each job and schedule type
print("\nAverage duration for each job and schedule type:")
job_schedule_avg_duration = df.groupby(['PRCSNAME', 'SCHEDULE'])['ACTUAL_DURATION'].mean().sort_values(ascending=False)
for (job, schedule), avg_duration in job_schedule_avg_duration.items():
    category = job_categories[job]
    impact = job_impacts[job]
    print(f"{job}: {category} ({impact}, {schedule}) - Avg Duration: {avg_duration:.2f} min")

# Display distribution of schedule types
print("\nDistribution of schedule types:")
schedule_counts = df['SCHEDULE'].value_counts()
for schedule, count in schedule_counts.items():
    print(f"{schedule}: {count} ({count / len(df) * 100:.2f}%)")

# Verify timestamp consistency
print("\nVerifying timestamp consistency:")
print(f"Negative durations: {(df['ACTUAL_DURATION'] < 0).sum()}")
print(f"Begin time before request time: {(df['BEGINDTTM'] < df['RQSTDTTM']).sum()}")
print(f"End time before begin time: {(df['ENDDTTM'] < df['BEGINDTTM']).sum()}")

count    1000000.000000
mean          37.102147
std          256.764462
min            0.016667
25%            0.716667
50%            1.450000
75%            5.283333
max         4319.566667
Name: ACTUAL_DURATION, dtype: float64

Total jobs: 1000000
Jobs before upgrade: 884745 (88.47%)
Jobs after upgrade: 115255 (11.53%)

Job duration distribution for scheduler jobs:
Under 2 minutes: 112799 (67.79%)
2 to 15 minutes: 44275 (26.61%)
15 minutes to 4 hours: 4934 (2.97%)
4 hours to 1 day: 3441 (2.07%)
1 day to 3 days: 950 (0.57%)

Job duration distribution for non-scheduler jobs:
Under 2 minutes: 565655 (67.86%)
2 to 15 minutes: 221966 (26.63%)
15 minutes to 4 hours: 24155 (2.90%)
4 hours to 1 day: 16909 (2.03%)
1 day to 3 days: 4916 (0.59%)

Average duration for each job and schedule type:
JOB_165: very_long (improved, unscheduled) - Avg Duration: 2782.86 min
JOB_2: long (improved, unscheduled) - Avg Duration: 702.29 min
JOB_70: long (improved, daily) - Avg Duration: 700.82 min
JOB_145: l

In [3]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load and preprocess your data
file_path = 'synth_job_performance_data.csv'
df = pd.read_csv(file_path)

# Convert date columns to datetime
df['RQSTDTTM'] = pd.to_datetime(df['RQSTDTTM'])
df['BEGINDTTM'] = pd.to_datetime(df['BEGINDTTM'])
df['ENDDTTM'] = pd.to_datetime(df['ENDDTTM'])

# Calculate durations and request to begin time
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-05-19')

# Aggregate to weekly intervals
df.set_index('BEGINDTTM', inplace=True)
weekly_avg = df.groupby(['PRCSNAME', pd.Grouper(freq='W')])['DURATION'].mean().reset_index()
weekly_avg['UPGRADE'] = weekly_avg['BEGINDTTM'] >= pd.Timestamp('2024-05-19')

# Separate pre and post-upgrade data
pre_upgrade = weekly_avg[weekly_avg['UPGRADE'] == False]
post_upgrade = weekly_avg[weekly_avg['UPGRADE'] == True]

# Calculate IQR
pre_iqr = pre_upgrade.groupby('PRCSNAME')['DURATION'].apply(lambda x: x.quantile(0.75) - x.quantile(0.25)).reset_index(name='IQR_Pre')
post_iqr = post_upgrade.groupby('PRCSNAME')['DURATION'].apply(lambda x: x.quantile(0.75) - x.quantile(0.25)).reset_index(name='IQR_Post')

# Merge pre and post-upgrade IQR data
comparison_iqr = pd.merge(pre_iqr, post_iqr, on='PRCSNAME', suffixes=('_Pre', '_Post'))

# Create main scatter plot
scatter_fig = px.scatter(comparison_iqr, x='IQR_Pre', y='IQR_Post', color='PRCSNAME',
                         title='IQR of Job Durations Pre vs. Post Upgrade',
                         labels={'IQR_Pre': 'IQR Pre-Upgrade (minutes)', 'IQR_Post': 'IQR Post-Upgrade (minutes)'},
                         hover_data=['PRCSNAME'])

# Add line of equality (y=x) to show no change
scatter_fig.add_shape(
    type='line',
    line=dict(dash='dash'),
    x0=0, y0=0,
    x1=comparison_iqr['IQR_Pre'].max(),
    y1=comparison_iqr['IQR_Pre'].max()
)

# Create subplots layout
fig = make_subplots(rows=2, cols=1, shared_xaxes=True,
                    subplot_titles=['IQR of Job Durations Pre vs. Post Upgrade', 'Duration Over Time'])

# Add scatter plot to subplot
fig.add_trace(scatter_fig.data[0], row=1, col=1)

# Function to create a time series plot
def create_time_series(dff, title):
    return px.line(dff, x='BEGINDTTM', y='DURATION', title=title).data[0]

# Add a time series plot for a selected job to the subplot
selected_job = comparison_iqr['PRCSNAME'].unique()[0]
dff = weekly_avg[weekly_avg['PRCSNAME'] == selected_job]
time_series = create_time_series(dff, f'<b>{selected_job}</b><br>Duration over Time')

fig.add_trace(time_series, row=2, col=1)

# Update layout to add dropdown and callback functionality
fig.update_layout(
    updatemenus=[
        {
            "buttons": [
                {
                    "label": job,
                    "method": "update",
                    "args": [
                        {
                            "visible": [True, *(comparison_iqr['PRCSNAME'] == job)]
                        },
                        {
                            "title": f'<b>{job}</b><br>Duration over Time'
                        }
                    ]
                }
                for job in comparison_iqr['PRCSNAME'].unique()
            ],
            "direction": "down",
            "showactive": True,
            "x": 0.17,
            "xanchor": "left",
            "y": 1.15,
            "yanchor": "top"
        }
    ]
)

# Update subplot layout
fig.update_layout(height=800, width=1000, title_text="Job Performance Dashboard")

# Save as interactive HTML
fig.write_html("job_performance_dashboard.html")

print("Dashboard saved as 'job_performance_dashboard.html'")

Dashboard saved as 'job_performance_dashboard.html'


In [34]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load your data
# Assuming df is your DataFrame with the job data
# If it's not already loaded, you'll need to load it here
# df = pd.read_csv('your_data.csv')  # Uncomment and modify this line if needed

# Convert BEGINDTTM to datetime if it's not already
#df['BEGINDTTM'] = pd.to_datetime(df['BEGINDTTM'])

# Resample data to daily average duration for each job
daily_avg = df.groupby([df['BEGINDTTM'].dt.date, 'PRCSNAME'])['ACTUAL_DURATION'].mean().reset_index()
daily_avg['BEGINDTTM'] = pd.to_datetime(daily_avg['BEGINDTTM'])

# Get list of unique job names
job_names = df['PRCSNAME'].unique().tolist()

# Create the plot
fig = make_subplots(specs=[[{"secondary_y": False}]])

# Add traces for each job
for job in job_names:
    job_data = daily_avg[daily_avg['PRCSNAME'] == job]
    fig.add_trace(
        go.Scatter(x=job_data['BEGINDTTM'], y=job_data['ACTUAL_DURATION'],
                   mode='lines', name=job, visible='legendonly')
    )

# Add vertical line for upgrade date
upgrade_date = pd.Timestamp('2024-05-19')
fig.add_vline(x=upgrade_date, line_width=2, line_dash="dash", line_color="red")

# Update layout
fig.update_layout(
    title='Average Job Duration Over Time',
    xaxis_title='Date',
    yaxis_title='Average Duration (minutes)',
    height=600,
    width=1000,
    legend_title="Select Jobs:",
    updatemenus=[
        dict(
            type="buttons",
            direction="left",
            buttons=[
                dict(label="Select All",
                     method="update",
                     args=[{"visible": [True] * len(job_names)},
                           {"title": "Average Job Duration Over Time"}]),
                dict(label="Deselect All",
                     method="update",
                     args=[{"visible": [False] * len(job_names)},
                           {"title": "Average Job Duration Over Time"}]),
            ],
            pad={"r": 10, "t": 10},
            showactive=False,
            x=0.11,
            xanchor="left",
            y=1.1,
            yanchor="top"
        ),
    ]
)

# Save as interactive HTML
fig.write_html("job_performance_dashboard.html")

print("Dashboard saved as 'job_performance_dashboard.html'")

Dashboard saved as 'job_performance_dashboard.html'


In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# Load and preprocess your data
file_path = 'synth_job_performance_data.csv'
df = pd.read_csv(file_path)

# Convert date columns to datetime
df['RQSTDTTM'] = pd.to_datetime(df['RQSTDTTM'])
df['BEGINDTTM'] = pd.to_datetime(df['BEGINDTTM'])
df['ENDDTTM'] = pd.to_datetime(df['ENDDTTM'])

# Calculate durations and request to begin time
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-05-19')

# Aggregate to weekly intervals
df.set_index('BEGINDTTM', inplace=True)
weekly_avg = df.groupby(['PRCSNAME', pd.Grouper(freq='W')])['DURATION'].mean().reset_index()
weekly_avg['UPGRADE'] = weekly_avg['BEGINDTTM'] >= pd.Timestamp('2024-05-19')

# Separate pre and post-upgrade data
pre_upgrade = weekly_avg[weekly_avg['UPGRADE'] == False]
post_upgrade = weekly_avg[weekly_avg['UPGRADE'] == True]

# Calculate IQR
pre_iqr = pre_upgrade.groupby('PRCSNAME')['DURATION'].apply(lambda x: x.quantile(0.75) - x.quantile(0.25)).reset_index(name='IQR_Pre')
post_iqr = post_upgrade.groupby('PRCSNAME')['DURATION'].apply(lambda x: x.quantile(0.75) - x.quantile(0.25)).reset_index(name='IQR_Post')

# Merge pre and post-upgrade IQR data
comparison_iqr = pd.merge(pre_iqr, post_iqr, on='PRCSNAME', suffixes=('_Pre', '_Post'))

# Create scatter plot
fig = px.scatter(comparison_iqr, x='IQR_Pre', y='IQR_Post', color='PRCSNAME',
                 title='IQR of Job Durations Pre vs. Post Upgrade',
                 labels={'IQR_Pre': 'IQR Pre-Upgrade (minutes)', 'IQR_Post': 'IQR Post-Upgrade (minutes)'},
                 hover_data=['PRCSNAME'])

# Add line of equality (y=x) to show no change
fig.add_shape(
    type='line',
    line=dict(dash='dash'),
    x0=0, y0=0,
    x1=comparison_iqr['IQR_Pre'].max(),
    y1=comparison_iqr['IQR_Pre'].max()
)

# Create time series plot for job duration over time
def create_time_series(dff, title):
    fig = px.line(dff, x='BEGINDTTM', y='DURATION', title=title)
    fig.update_xaxes(showgrid=False)
    fig.update_yaxes(showgrid=False)
    fig.update_layout(margin={'l': 20, 'b': 30, 'r': 10, 't': 10})
    return fig

# Save the scatter plot as an interactive HTML file
fig.write_html("iqr_comparison.html")

# Create the time series plot for each job and save as HTML files
for job_name in comparison_iqr['PRCSNAME'].unique():
    dff = weekly_avg[weekly_avg['PRCSNAME'] == job_name]
    title = f'<b>{job_name}</b><br>Duration over Time'
    time_series_fig = create_time_series(dff, title)
    time_series_fig.write_html(f"time_series_{job_name}.html")

# Print confirmation
print("Scatter plot saved as 'iqr_comparison.html' and time series plots saved as 'time_series_<job_name>.html'")



Scatter plot saved as 'iqr_comparison.html' and time series plots saved as 'time_series_<job_name>.html'


In [23]:
df.drop(columns=['IS_AFTER_UPGRADE','SCHEDULE'],inplace=True)
df.drop(columns=['ACTUAL_DURATION'],inplace=True)

In [20]:
df.head().to_clipboard()

In [35]:
df.to_csv('synth_job_performance_data.csv', index=False)

In [43]:
df.sample(500000).to_csv('synth_job_performance_data_sample.csv', index=False)

In [6]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def categorize_jobs(df):
    def categorize_single_job(job_df):
        # Convert to datetime if not already
        job_df['RQSTDTTM'] = pd.to_datetime(job_df['RQSTDTTM'])
        
        # Sort by request time
        job_df = job_df.sort_values('RQSTDTTM')
        
        # Calculate time differences
        time_diffs = job_df['RQSTDTTM'].diff()
        
        # Calculate the most common time difference
        most_common_diff = time_diffs.mode().iloc[0]
        
        # Categorize based on the most common time difference
        if most_common_diff <= pd.Timedelta(minutes=20):
            return '15min'
        elif most_common_diff <= pd.Timedelta(hours=1):
            return 'hourly'
        elif most_common_diff <= pd.Timedelta(days=1):
            return 'daily'
        elif most_common_diff <= pd.Timedelta(days=7):
            return 'weekly'
        elif most_common_diff <= pd.Timedelta(days=31):
            return 'monthly'
        else:
            return 'irregular'

    # Group by PRCSNAME and apply the categorization function
    job_categories = df.groupby('PRCSNAME').apply(categorize_single_job)
    
    # Add the category back to the original DataFrame
    df['SCHEDULE'] = df['PRCSNAME'].map(job_categories)
    
    return df

def create_dashboard(df):
    # Categorize jobs
    df = categorize_jobs(df)

    # Create IS_AFTER_UPGRADE column
    upgrade_date = pd.Timestamp('2024-05-19')
    df['IS_AFTER_UPGRADE'] = df['RQSTDTTM'] >= upgrade_date

    # Create a subplot figure
    fig = make_subplots(
        rows=3, cols=2,
        subplot_titles=(
            "Average Job Duration Over Time",
            "Job Duration Distribution by Schedule Type",
            "Top 10 Most Improved Jobs",
            "Top 10 Most Regressed Jobs",
            "Error Rate Before vs After Upgrade",
            "Interactive Job Performance Comparison"
        ),
        specs=[
            [{"type": "scatter"}, {"type": "box"}],
            [{"type": "bar"}, {"type": "bar"}],
            [{"type": "bar"}, {"type": "scatter"}]
        ],
        vertical_spacing=0.1,
        horizontal_spacing=0.05
    )

    # 1. Average Job Duration Over Time
    df['Date'] = pd.to_datetime(df['RQSTDTTM']).dt.date
    daily_avg = df.groupby('Date')['MINUTES'].mean().reset_index()
    fig.add_trace(
        go.Scatter(x=daily_avg['Date'], y=daily_avg['MINUTES'], mode='lines+markers', name='Avg Duration'),
        row=1, col=1
    )
    fig.add_vline(x=upgrade_date, line_dash="dash", line_color="red", row=1, col=1)

    # 2. Job Duration Distribution by Schedule Type
    for schedule in df['SCHEDULE'].unique():
        fig.add_trace(
            go.Box(y=df[(df['SCHEDULE'] == schedule) & (df['IS_AFTER_UPGRADE'] == False)]['MINUTES'], 
                   name=f'{schedule} Before', boxmean=True),
            row=1, col=2
        )
        fig.add_trace(
            go.Box(y=df[(df['SCHEDULE'] == schedule) & (df['IS_AFTER_UPGRADE'] == True)]['MINUTES'], 
                   name=f'{schedule} After', boxmean=True),
            row=1, col=2
        )

    # 3 & 4. Top 10 Most Improved and Regressed Jobs
    job_performance = df.groupby(['PRCSNAME', 'IS_AFTER_UPGRADE'])['MINUTES'].mean().unstack()
    job_performance['Percent_Change'] = (job_performance[True] - job_performance[False]) / job_performance[False] * 100
    improved = job_performance.nsmallest(10, 'Percent_Change')
    regressed = job_performance.nlargest(10, 'Percent_Change')

    fig.add_trace(
        go.Bar(x=improved.index, y=improved['Percent_Change'], name='Improved', marker_color='green'),
        row=2, col=1
    )
    fig.add_trace(
        go.Bar(x=regressed.index, y=regressed['Percent_Change'], name='Regressed', marker_color='red'),
        row=2, col=2
    )

    # 5. Error Rate Before vs After Upgrade
    error_rate = df.groupby('IS_AFTER_UPGRADE')['RUNSTATUSDESC'].apply(lambda x: (x == 'Error').mean() * 100)
    fig.add_trace(
        go.Bar(x=['Before Upgrade', 'After Upgrade'], y=error_rate, name='Error Rate'),
        row=3, col=1
    )

    # 6. Interactive Job Performance Comparison
    job_performances = df.groupby('PRCSNAME').agg({
        'MINUTES': [
            ('Before', lambda x: x[~df['IS_AFTER_UPGRADE']].mean()),
            ('After', lambda x: x[df['IS_AFTER_UPGRADE']].mean())
        ]
    }).reset_index()

    # Flatten the column names
    job_performances.columns = ['PRCSNAME', 'MINUTES_BEFORE', 'MINUTES_AFTER']

    fig.add_trace(
        go.Scatter(
            x=job_performances['MINUTES_BEFORE'],
            y=job_performances['MINUTES_AFTER'],
            mode='markers',
            marker=dict(size=8, color='blue', opacity=0.6),
            name='All Jobs',
            text=job_performances['PRCSNAME'],
            hoverinfo='text',
            hovertemplate='%{text}<br>Before: %{x:.2f} min<br>After: %{y:.2f} min'
        ),
        row=3, col=2
    )

    # Update layout (same as before)
    # ...

    # Save the figure as an interactive HTML file
    fig.write_html("job_performance_dashboard.html")

    print("Dashboard has been generated and saved as 'job_performance_dashboard.html'")

# Example usage:
# df = pd.read_csv('your_data.csv')  # Load your data
create_dashboard(df)

Dashboard has been generated and saved as 'job_performance_dashboard.html'


In [7]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Convert date columns to datetime
df['RQSTDTTM'] = pd.to_datetime(df['RQSTDTTM'])
df['BEGINDTTM'] = pd.to_datetime(df['BEGINDTTM'])
df['ENDDTTM'] = pd.to_datetime(df['ENDDTTM'])

# Calculate durations and request to begin time
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-05-19')

# Aggregate to weekly intervals
df.set_index('BEGINDTTM', inplace=True)
weekly_avg = df.groupby(['PRCSNAME', pd.Grouper(freq='W')])['DURATION'].mean().reset_index()
weekly_avg['UPGRADE'] = weekly_avg['BEGINDTTM'] >= pd.Timestamp('2024-05-19')

# Separate pre and post-upgrade data
pre_upgrade = weekly_avg[weekly_avg['UPGRADE'] == False]
post_upgrade = weekly_avg[weekly_avg['UPGRADE'] == True]

# Calculate IQR
pre_iqr = pre_upgrade.groupby('PRCSNAME')['DURATION'].apply(lambda x: x.quantile(0.75) - x.quantile(0.25)).reset_index(name='IQR_Pre')
post_iqr = post_upgrade.groupby('PRCSNAME')['DURATION'].apply(lambda x: x.quantile(0.75) - x.quantile(0.25)).reset_index(name='IQR_Post')

# Merge pre and post-upgrade IQR data
comparison_iqr = pd.merge(pre_iqr, post_iqr, on='PRCSNAME', suffixes=('_Pre', '_Post'))
comparison_iqr['Difference (minutes)'] = comparison_iqr['IQR_Post'] - comparison_iqr['IQR_Pre']
comparison_iqr['Improvement (%)'] = (comparison_iqr['Difference (minutes)'] / comparison_iqr['IQR_Pre']) * -100
comparison_iqr['Change'] = comparison_iqr['Difference (minutes)'].apply(lambda x: 'Improvement' if x < 0 else 'Regression' if x > 0 else 'No Change')

# Sort by improvement/regression
comparison_iqr = comparison_iqr.sort_values('Difference (minutes)')

# Create subplots layout
fig = make_subplots(
    rows=3, cols=1,
    shared_xaxes=True,
    vertical_spacing=0.03,
    specs=[[{"type": "table"}],
           [{"type": "scatter"}],
           [{"type": "scatter"}]]
)

# Add table trace
fig.add_trace(
    go.Table(
        header=dict(
            values=["Job Name", "IQR Pre-Upgrade (minutes)", "IQR Post-Upgrade (minutes)", 
                    "Difference (minutes)", "Improvement (%)"],
            font=dict(size=10),
            align="left"
        ),
        cells=dict(
            values=[comparison_iqr[k].tolist() for k in comparison_iqr.columns],
            align="left")
    ),
    row=1, col=1
)

# Add scatter plot trace
scatter_fig = px.scatter(comparison_iqr, x='IQR_Pre', y='IQR_Post', color='Change',
                         title='IQR of Job Durations Pre vs. Post Upgrade',
                         labels={'IQR_Pre': 'IQR Pre-Upgrade (minutes)', 'IQR_Post': 'IQR Post-Upgrade (minutes)'},
                         hover_data=['PRCSNAME', 'Difference (minutes)', 'Improvement (%)'])

# Add line of equality (y=x) to show no change
scatter_fig.add_shape(
    type='line',
    line=dict(dash='dash'),
    x0=0, y0=0,
    x1=comparison_iqr['IQR_Pre'].max(),
    y1=comparison_iqr['IQR_Pre'].max()
)

for trace in scatter_fig['data']:
    fig.add_trace(trace, row=2, col=1)

# Function to create a time series plot
def create_time_series(dff, title):
    fig = px.line(dff, x='BEGINDTTM', y='DURATION', title=title)
    fig.update_xaxes(showgrid=False)
    fig.update_yaxes(showgrid=False)
    fig.update_layout(margin={'l': 20, 'b': 30, 'r': 10, 't': 10})
    return fig

# Add a time series plot for the most improved job
most_improved_job = comparison_iqr.iloc[0]['PRCSNAME']
dff = weekly_avg[weekly_avg['PRCSNAME'] == most_improved_job]
time_series = create_time_series(dff, f'<b>{most_improved_job}</b><br>Duration over Time')

for trace in time_series['data']:
    fig.add_trace(trace, row=3, col=1)

# Update layout
fig.update_layout(
    height=1200,
    showlegend=False,
    title_text="Job Performance Dashboard",
    hovermode='closest'
)

# Add dropdown menu for job selection to update the time series plot
dropdown_buttons = [
    dict(label=job, method="update", args=[
        {"visible": [True]*len(fig.data)},
        {"title": f'<b>{job}</b><br>Duration over Time'}
    ]) for job in comparison_iqr['PRCSNAME'].unique()
]

fig.update_layout(
    updatemenus=[
        dict(
            buttons=dropdown_buttons,
            direction="down",
            showactive=True,
            x=0.17,
            xanchor="left",
            y=1.1,
            yanchor="top"
        )
    ]
)

# Save as interactive HTML
fig.write_html("job_matrix_performance_dashboard.html")

print("Dashboard saved as 'job_matrix_performance_dashboard.html'")

Dashboard saved as 'job_matrix_performance_dashboard.html'


In [26]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

def create_outlier_adjusted_dashboard(df):
    # Ensure 'MINUTES' column exists and is calculated correctly
    df['MINUTES'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60
    
    # Create IS_AFTER_UPGRADE column
    upgrade_date = pd.Timestamp('2024-06-01')
    df['IS_AFTER_UPGRADE'] = df['RQSTDTTM'] >= upgrade_date

    # Calculate job performances
    job_performances = df.groupby('PRCSNAME').agg({
        'MINUTES': [
            ('Before', lambda x: max(x[~df['IS_AFTER_UPGRADE']].mean(), 0.1)),
            ('After', lambda x: max(x[df['IS_AFTER_UPGRADE']].mean(), 0.1))
        ]
    }).reset_index()

    # Flatten column names
    job_performances.columns = ['PRCSNAME', 'MINUTES_BEFORE', 'MINUTES_AFTER']
    
    # Calculate percentage change
    job_performances['Percent_Change'] = ((job_performances['MINUTES_AFTER'] - job_performances['MINUTES_BEFORE']) / job_performances['MINUTES_BEFORE']) * 100
    
    # Function to calculate axis limits
    def calculate_axis_limits(data):
        q1, q3 = np.percentile(data, [25, 75])
        iqr = q3 - q1
        lower_bound = max(q1 - 1.5 * iqr, data.min())
        upper_bound = min(q3 + 1.5 * iqr, data.max())
        return lower_bound, upper_bound

    x_min, x_max = calculate_axis_limits(job_performances['MINUTES_BEFORE'])
    y_min, y_max = calculate_axis_limits(job_performances['MINUTES_AFTER'])

    # Create the main figure
    fig = go.Figure()

    # Add scatter plot
    fig.add_trace(go.Scatter(
        x=job_performances['MINUTES_BEFORE'],
        y=job_performances['MINUTES_AFTER'],
        mode='markers',
        marker=dict(
            size=10,
            color=job_performances['Percent_Change'],
            colorscale='RdYlGn_r',
            colorbar=dict(title="% Change"),
            cmin=-50,
            cmax=50,
            showscale=True
        ),
        text=job_performances['PRCSNAME'],
        hovertemplate="<b>%{text}</b><br>Before: %{x:.2f} min<br>After: %{y:.2f} min<br>Change: %{marker.color:.1f}%<extra></extra>"
    ))

    # Add line of equality
    fig.add_trace(go.Scatter(
        x=[min(x_min, y_min), max(x_max, y_max)],
        y=[min(x_min, y_min), max(x_max, y_max)],
        mode='lines',
        line=dict(color='gray', dash='dash'),
        showlegend=False
    ))

    # Calculate percentage of improved jobs
    pct_improved = (job_performances['Percent_Change'] < 0).mean() * 100
    total_jobs = len(job_performances)

    # Update layout
    fig.update_layout(
        title=f"Job Completion Times Pre vs. Post Upgrade<br><sup>{pct_improved:.1f}% of {total_jobs} jobs improved</sup>",
        xaxis_title="Pre-Upgrade Average Job Duration (minutes, log scale)",
        yaxis_title="Post-Upgrade Average Job Duration (minutes, log scale)",
        xaxis_type="log",
        yaxis_type="log",
        xaxis=dict(range=[np.log10(x_min*0.9), np.log10(x_max*1.1)]),
        yaxis=dict(range=[np.log10(y_min*0.9), np.log10(y_max*1.1)]),
        height=800,
        width=1000,
        hovermode='closest'
    )

    # Add annotations for extreme cases
    extreme_improvement = job_performances.loc[job_performances['Percent_Change'].idxmin()]
    extreme_regression = job_performances.loc[job_performances['Percent_Change'].idxmax()]

    for extreme in [extreme_improvement, extreme_regression]:
        if x_min <= extreme['MINUTES_BEFORE'] <= x_max and y_min <= extreme['MINUTES_AFTER'] <= y_max:
            fig.add_annotation(
                x=extreme['MINUTES_BEFORE'],
                y=extreme['MINUTES_AFTER'],
                text=f"{'Most Improved' if extreme['Percent_Change'] < 0 else 'Most Regressed'}: {extreme['PRCSNAME']}<br>{abs(extreme['Percent_Change']):.1f}% {'faster' if extreme['Percent_Change'] < 0 else 'slower'}",
                showarrow=True,
                arrowhead=2,
                arrowsize=1,
                arrowwidth=2,
                arrowcolor="#00CC96" if extreme['Percent_Change'] < 0 else "#EF553B"
            )

    # Save the figure as an interactive HTML file
    fig.write_html("outlier_adjusted_job_performance_dashboard.html")

    print("Outlier-adjusted dashboard has been generated and saved as 'outlier_adjusted_job_performance_dashboard.html'")

# Assuming df is your DataFrame with the required columns
create_outlier_adjusted_dashboard(df)

Outlier-adjusted dashboard has been generated and saved as 'outlier_adjusted_job_performance_dashboard.html'


In [27]:
df[df['PRCSNAME'] == 'JOB_155']

RQSTDTTM PRCSNAME  SECONDS   MINUTES RUNSTATUSDESC  \
368    2024-03-07 16:02:50  JOB_155       94  1.566667       Success   
995    2024-01-25 11:49:55  JOB_155       42  0.700000       Success   
1029   2023-11-21 05:59:44  JOB_155       16  0.266667       Success   
1253   2024-03-20 12:56:24  JOB_155        7  0.116667       Success   
1290   2024-02-01 06:40:11  JOB_155        4  0.066667       Success   
...                    ...      ...      ...       ...           ...   
998993 2024-06-21 21:15:00  JOB_155       34  0.566667       Success   
999332 2024-06-01 12:27:37  JOB_155       89  1.483333       Success   
999611 2024-06-09 14:16:09  JOB_155       60  1.000000       Success   
999662 2024-05-22 10:50:01  JOB_155       28  0.466667       Success   
999712 2024-06-16 14:27:44  JOB_155       50  0.833333       Success   

        PRCSINSTANCE      OPRID          RUNCNTLID           BEGINDTTM  \
368           863995     asmith  EXTERNAL_PAYMENTS 2024-03-07 16:04:03   
995           589083   bjohnson  INTERNAL_PAYMENTS 2024-01-25 11:51:05   
1029          477985     asmith  EXTERNAL_PAYMENTS 2023-11-21 06:00:29   
1253          757713   bjohnson  INTERNAL_PAYMENTS 2024-03-20 12:59:40   
1290          786462    mcurtis  EXTERNAL_PAYMENTS 2024-02-01 06:43:31   
...              ...        ...                ...                 ...   
998993        385954  scheduler  INTERNAL_PAYMENTS 2024-06-21 21:16:46   
999332        971507       jdoe  INTERNAL_PAYMENTS 2024-06-01 12:30:46   
999611        566608       jdoe  EXTERNAL_PAYMENTS 2024-06-09 14:18:17   
999662        992617     asmith  EXTERNAL_PAYMENTS 2024-05-22 10:51:45   
999712        638050       jdoe  EXTERNAL_PAYMENTS 2024-06-16 14:30:00   

                   ENDDTTM SCHEDULE  IS_AFTER_UPGRADE        Date  
368    2024-03-07 16:05:37    15min             False  2024-03-07  
995    2024-01-25 11:51:47    15min             False  2024-01-25  
1029   2023-11-21 06:00:45    15min             False  2023-11-21  
1253   2024-03-20 12:59:47    15min             False  2024-03-20  
1290   2024-02-01 06:43:35    15min             False  2024-02-01  
...                    ...      ...               ...         ...  
998993 2024-06-21 21:17:20    15min              True  2024-06-21  
999332 2024-06-01 12:32:15    15min              True  2024-06-01  
999611 2024-06-09 14:19:17    15min              True  2024-06-09  
999662 2024-05-22 10:52:13    15min             False  2024-05-22  
999712 2024-06-16 14:30:50    15min              True  2024-06-16  

[6093 rows x 13 columns]

In [28]:
extreme_improvement

PRCSNAME                    JOB_143
DURATION_Pre               5.892043
DURATION_Post              3.192498
Difference (minutes)      -2.699545
Improvement (%)           45.816793
Change                  Improvement
Name: 49, dtype: object

In [5]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px
import numpy as np

def create_dashboard(df):
    # Create a subplot figure
    fig = make_subplots(
        rows=3, cols=2,
        subplot_titles=(
            "Average Job Duration Over Time",
            "Job Duration Distribution by Schedule Type",
            "Top 10 Most Improved Jobs",
            "Top 10 Most Regressed Jobs",
            "Error Rate Before vs After Upgrade",
            "Interactive Job Performance Comparison"
        ),
        specs=[
            [{"type": "scatter"}, {"type": "box"}],
            [{"type": "bar"}, {"type": "bar"}],
            [{"type": "bar"}, {"type": "scatter"}]
        ],
        vertical_spacing=0.1,
        horizontal_spacing=0.05
    )

    # 1. Average Job Duration Over Time
    df['Date'] = pd.to_datetime(df['RQSTDTTM']).dt.date
    daily_avg = df.groupby('Date')['MINUTES'].mean().reset_index()
    fig.add_trace(
        go.Scatter(x=daily_avg['Date'], y=daily_avg['MINUTES'], mode='lines+markers', name='Avg Duration'),
        row=1, col=1
    )
    fig.add_vline(x=pd.Timestamp('2024-05-19'), line_dash="dash", line_color="red", row=1, col=1)

    # 2. Job Duration Distribution by Schedule Type
    for schedule in df['SCHEDULE'].unique():
        fig.add_trace(
            go.Box(y=df[(df['SCHEDULE'] == schedule) & (df['IS_AFTER_UPGRADE'] == False)]['MINUTES'], 
                   name=f'{schedule} Before', boxmean=True),
            row=1, col=2
        )
        fig.add_trace(
            go.Box(y=df[(df['SCHEDULE'] == schedule) & (df['IS_AFTER_UPGRADE'] == True)]['MINUTES'], 
                   name=f'{schedule} After', boxmean=True),
            row=1, col=2
        )

    # 3 & 4. Top 10 Most Improved and Regressed Jobs
    job_performance = df.groupby(['PRCSNAME', 'IS_AFTER_UPGRADE'])['MINUTES'].mean().unstack()
    job_performance['Percent_Change'] = (job_performance[True] - job_performance[False]) / job_performance[False] * 100
    improved = job_performance.nsmallest(10, 'Percent_Change')
    regressed = job_performance.nlargest(10, 'Percent_Change')

    fig.add_trace(
        go.Bar(x=improved.index, y=improved['Percent_Change'], name='Improved', marker_color='green'),
        row=2, col=1
    )
    fig.add_trace(
        go.Bar(x=regressed.index, y=regressed['Percent_Change'], name='Regressed', marker_color='red'),
        row=2, col=2
    )

    # 5. Error Rate Before vs After Upgrade
    error_rate = df.groupby('IS_AFTER_UPGRADE')['RUNSTATUSDESC'].apply(lambda x: (x == 'Error').mean() * 100)
    fig.add_trace(
        go.Bar(x=['Before Upgrade', 'After Upgrade'], y=error_rate, name='Error Rate'),
        row=3, col=1
    )

# 6. Interactive Job Performance Comparison
    job_list = df['PRCSNAME'].unique().tolist()
    
    job_performances = df.groupby('PRCSNAME').agg({
        'MINUTES': lambda x: x[~df['IS_AFTER_UPGRADE']].mean(),
        'MINUTES_AFTER': lambda x: x[df['IS_AFTER_UPGRADE']].mean()
    }).reset_index()

    fig.add_trace(
        go.Scatter(
            x=job_performances['MINUTES'],
            y=job_performances['MINUTES_AFTER'],
            mode='markers',
            marker=dict(size=8, color='blue', opacity=0.6),
            name='All Jobs',
            text=job_performances['PRCSNAME'],
            hoverinfo='text',
            hovertemplate='%{text}<br>Before: %{x:.2f} min<br>After: %{y:.2f} min'
        ),
        row=3, col=2
    )

    # Update layout
    fig.update_layout(
        height=1080, 
        width=1920, 
        title_text="Job Performance Upgrade Dashboard",
        showlegend=False,
        updatemenus=[
            dict(
                buttons=[
                    dict(label="All Jobs",
                         method="update",
                         args=[{"marker.color": ["blue"] * len(job_performances),
                                "marker.size": [8] * len(job_performances),
                                "marker.opacity": [0.6] * len(job_performances)}]),
                    *[dict(label=job,
                           method="update",
                           args=[{"marker.color": ["red" if j == job else "blue" for j in job_performances['PRCSNAME']],
                                  "marker.size": [12 if j == job else 8 for j in job_performances['PRCSNAME']],
                                  "marker.opacity": [1 if j == job else 0.3 for j in job_performances['PRCSNAME']]}])
                      for job in job_list]
                ],
                direction="down",
                pad={"r": 10, "t": 10},
                showactive=True,
                x=0.9,
                xanchor="left",
                y=0.2,
                yanchor="top"
            ),
        ]
    )

    # (Rest of the layout updates remain the same)

    # Add diagonal line for reference
    fig.add_trace(
        go.Scatter(x=[0.1, 10000], y=[0.1, 10000], mode='lines', line=dict(dash='dash'), 
                   name='No Change Line', showlegend=False),
        row=3, col=2
    )

    # Save the figure as an interactive HTML file
    fig.write_html("job_performance_dashboard.html")

    print("Dashboard has been generated and saved as 'job_performance_dashboard.html'")

# Assuming df is your DataFrame from the previous data generation step
create_dashboard(df)

KeyError: "Column(s) ['MINUTES_AFTER'] do not exist"

In [2]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Generate synthetic data
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations and request to begin time
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds()
df['REQUEST_TO_BEGIN'] = (df['BEGINDTTM'] - df['RQSTDTTM']).dt.total_seconds()
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME').agg({'DURATION': ['mean', 'std'], 'REQUEST_TO_BEGIN': ['mean', 'std']}).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME').agg({'DURATION': ['mean', 'std'], 'REQUEST_TO_BEGIN': ['mean', 'std']}).reset_index()

# Flatten MultiIndex columns
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Mean Duration', 'Pre-Upgrade Std Duration', 'Pre-Upgrade Mean Request to Begin', 'Pre-Upgrade Std Request to Begin']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Mean Duration', 'Post-Upgrade Std Duration', 'Post-Upgrade Mean Request to Begin', 'Post-Upgrade Std Request to Begin']

# Merge pre and post upgrade stats
stats_comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME', how='outer')

# Interactive dropdown plot
fig = make_subplots(rows=2, cols=1, subplot_titles=("Duration Comparison", "Request to Begin Time Comparison"))

# Create traces for each job
traces_duration = []
traces_request_to_begin = []

for job in stats_comparison['PRCSNAME']:
    job_data = stats_comparison[stats_comparison['PRCSNAME'] == job]
    trace_duration = go.Bar(
        x=['Pre-Upgrade', 'Post-Upgrade'],
        y=[job_data['Pre-Upgrade Mean Duration'].values[0], job_data['Post-Upgrade Mean Duration'].values[0]],
        name=job,
        error_y=dict(type='data', array=[job_data['Pre-Upgrade Std Duration'].values[0], job_data['Post-Upgrade Std Duration'].values[0]])
    )
    traces_duration.append(trace_duration)

    trace_request_to_begin = go.Bar(
        x=['Pre-Upgrade', 'Post-Upgrade'],
        y=[job_data['Pre-Upgrade Mean Request to Begin'].values[0], job_data['Post-Upgrade Mean Request to Begin'].values[0]],
        name=job,
        error_y=dict(type='data', array=[job_data['Pre-Upgrade Std Request to Begin'].values[0], job_data['Post-Upgrade Std Request to Begin'].values[0]])
    )
    traces_request_to_begin.append(trace_request_to_begin)

# Add initial traces
fig.add_trace(traces_duration[0], row=1, col=1)
fig.add_trace(traces_request_to_begin[0], row=2, col=1)

# Update layout with dropdowns
fig.update_layout(
    updatemenus=[
        dict(
            active=0,
            buttons=list([
                dict(label=job,
                     method="update",
                     args=[{"visible": [i == idx for i in range(len(traces_duration))]},
                           {"title": f"Job: {job}"}])
                for idx, job in enumerate(stats_comparison['PRCSNAME'])
            ]),
            direction="down",
            pad={"r": 10, "t": 10},
            showactive=True,
            x=0.17,
            xanchor="left",
            y=1.15,
            yanchor="top"
        ),
    ]
)

# Show the plot
fig.update_layout(title_text="Pre and Post-Upgrade Job Comparisons")
fig.show()


In [3]:
df.head()

RQSTDTTM                     BEGINDTTM  \
0 2024-05-01 00:00:00.000000000 2024-05-01 00:03:00.000000000   
1 2024-05-01 01:20:57.831325301 2024-05-01 01:24:57.831325301   
2 2024-05-01 02:41:55.662650602 2024-05-01 02:42:55.662650602   
3 2024-05-01 04:02:53.493975903 2024-05-01 04:05:53.493975903   
4 2024-05-01 05:23:51.325301204 2024-05-01 05:26:51.325301204   

                        ENDDTTM  SECONDS  MINUTES PRCSNAME RUNSTATUSDESC  \
0 2024-05-01 00:09:00.000000000       54        4  JOB_130       Success   
1 2024-05-01 01:31:57.831325301       97        3   JOB_70       Success   
2 2024-05-01 02:46:55.662650602       96        1  JOB_145       Success   
3 2024-05-01 04:09:53.493975903      262        4  JOB_123         Error   
4 2024-05-01 05:29:51.325301204      138        2   JOB_89       Success   

   PRCSINSTANCE      OPRID          RUNCNTLID  DURATION  REQUEST_TO_BEGIN  \
0        971868  ewilliams  INTERNAL_PAYMENTS     360.0             180.0   
1        851496   bjohnson  EXTERNAL_PAYMENTS     420.0             240.0   
2        146403    mcurtis  INTERNAL_PAYMENTS     240.0              60.0   
3        715458    mcurtis  INTERNAL_PAYMENTS     240.0             180.0   
4        895600   bjohnson  EXTERNAL_PAYMENTS     180.0             180.0   

   UPGRADE  
0    False  
1    False  
2    False  
3    False  
4    False

In [16]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Generate synthetic data
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations and request to begin time
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds()
df['REQUEST_TO_BEGIN'] = (df['BEGINDTTM'] - df['RQSTDTTM']).dt.total_seconds()
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME').agg({'DURATION': ['mean', 'std'], 'REQUEST_TO_BEGIN': ['mean', 'std']}).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME').agg({'DURATION': ['mean', 'std'], 'REQUEST_TO_BEGIN': ['mean', 'std']}).reset_index()

# Flatten MultiIndex columns
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Mean Duration', 'Pre-Upgrade Std Duration', 'Pre-Upgrade Mean Request to Begin', 'Pre-Upgrade Std Request to Begin']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Mean Duration', 'Post-Upgrade Std Duration', 'Post-Upgrade Mean Request to Begin', 'Post-Upgrade Std Request to Begin']

# Merge pre and post upgrade stats
stats_comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME', how='outer')

# Create subplots
fig = make_subplots(rows=2, cols=1, subplot_titles=("Duration Comparison", "Request to Begin Time Comparison"))

# Create traces for each job
for job in stats_comparison['PRCSNAME']:
    job_data = stats_comparison[stats_comparison['PRCSNAME'] == job]
    trace_duration = go.Bar(
        x=['Pre-Upgrade', 'Post-Upgrade'],
        y=[job_data['Pre-Upgrade Mean Duration'].values[0], job_data['Post-Upgrade Mean Duration'].values[0]],
        name=job,
        error_y=dict(type='data', array=[job_data['Pre-Upgrade Std Duration'].values[0], job_data['Post-Upgrade Std Duration'].values[0]])
    )
    trace_request_to_begin = go.Bar(
        x=['Pre-Upgrade', 'Post-Upgrade'],
        y=[job_data['Pre-Upgrade Mean Request to Begin'].values[0], job_data['Post-Upgrade Mean Request to Begin'].values[0]],
        name=job,
        error_y=dict(type='data', array=[job_data['Pre-Upgrade Std Request to Begin'].values[0], job_data['Post-Upgrade Std Request to Begin'].values[0]])
    )
    fig.add_trace(trace_duration, row=1, col=1)
    fig.add_trace(trace_request_to_begin, row=2, col=1)

# Update layout with checkboxes
buttons = []
for i, job in enumerate(stats_comparison['PRCSNAME']):
    visible = [False] * len(stats_comparison['PRCSNAME']) * 2
    visible[i] = True
    visible[i + len(stats_comparison['PRCSNAME'])] = True
    buttons.append(dict(label=job,
                        method="update",
                        args=[{"visible": visible},
                              {"title": f"Job: {job}"}]))

# Adding "Select All" button
all_visible = [True] * len(stats_comparison['PRCSNAME']) * 2
buttons.append(dict(label="Select All",
                    method="update",
                    args=[{"visible": all_visible},
                          {"title": "All Jobs"}]))

fig.update_layout(
    updatemenus=[dict(
        type="buttons",
        direction="down",
        buttons=buttons,
        showactive=True,
    )],
    barmode='group'
)

# Show the plot
fig.update_layout(title_text="Pre and Post-Upgrade Job Comparisons")
fig.show()


In [15]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Generate synthetic data
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations and request to begin time
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds()
df['REQUEST_TO_BEGIN'] = (df['BEGINDTTM'] - df['RQSTDTTM']).dt.total_seconds()
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME').agg({'DURATION': ['mean', 'std'], 'REQUEST_TO_BEGIN': ['mean', 'std']}).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME').agg({'DURATION': ['mean', 'std'], 'REQUEST_TO_BEGIN': ['mean', 'std']}).reset_index()

# Flatten MultiIndex columns
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Mean Duration', 'Pre-Upgrade Std Duration', 'Pre-Upgrade Mean Request to Begin', 'Pre-Upgrade Std Request to Begin']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Mean Duration', 'Post-Upgrade Std Duration', 'Post-Upgrade Mean Request to Begin', 'Post-Upgrade Std Request to Begin']

# Merge pre and post upgrade stats
stats_comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME', how='outer')

# Create subplots
fig = make_subplots(rows=2, cols=1, subplot_titles=("Duration Comparison", "Request to Begin Time Comparison"))

# Create traces for each job
for job in stats_comparison['PRCSNAME']:
    job_data = stats_comparison[stats_comparison['PRCSNAME'] == job]
    trace_duration = go.Bar(
        x=['Pre-Upgrade', 'Post-Upgrade'],
        y=[job_data['Pre-Upgrade Mean Duration'].values[0], job_data['Post-Upgrade Mean Duration'].values[0]],
        name=job,
        error_y=dict(type='data', array=[job_data['Pre-Upgrade Std Duration'].values[0], job_data['Post-Upgrade Std Duration'].values[0]])
    )
    trace_request_to_begin = go.Bar(
        x=['Pre-Upgrade', 'Post-Upgrade'],
        y=[job_data['Pre-Upgrade Mean Request to Begin'].values[0], job_data['Post-Upgrade Mean Request to Begin'].values[0]],
        name=job,
        error_y=dict(type='data', array=[job_data['Pre-Upgrade Std Request to Begin'].values[0], job_data['Post-Upgrade Std Request to Begin'].values[0]])
    )
    fig.add_trace(trace_duration, row=1, col=1)
    fig.add_trace(trace_request_to_begin, row=2, col=1)

# Update layout with checkboxes
buttons = []
for i, job in enumerate(stats_comparison['PRCSNAME']):
    visible = [False] * len(stats_comparison['PRCSNAME']) * 2
    visible[i] = True
    visible[i + len(stats_comparison['PRCSNAME'])] = True
    buttons.append(dict(label=job,
                        method="update",
                        args=[{"visible": visible},
                              {"title": f"Job: {job}"}]))

# Adding "Select All" button
all_visible = [True] * len(stats_comparison['PRCSNAME']) * 2
buttons.append(dict(label="Select All",
                    method="update",
                    args=[{"visible": all_visible},
                          {"title": "All Jobs"}]))

fig.update_layout(
    updatemenus=[dict(
        type="buttons",
        direction="down",
        buttons=buttons,
        showactive=True,
    )],
    barmode='group',
    autosize=True,
    height=800,  # Adjust as needed for full screen
    width=1200   # Adjust as needed for full screen
)

# Make the plot responsive
fig.update_layout(
    title_text="Pre and Post-Upgrade Job Comparisons",
    margin=dict(l=0, r=0, t=0, b=0),
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
    xaxis=dict(fixedrange=True),
    yaxis=dict(fixedrange=True)
)

fig.show()


In [18]:
import pandas as pd
import numpy as np
import plotly.express as px

# Generate synthetic data
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations and request to begin time
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds()
df['REQUEST_TO_BEGIN'] = (df['BEGINDTTM'] - df['RQSTDTTM']).dt.total_seconds()
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Melt the data for Plotly Express
df_melted = df.melt(id_vars=['PRCSNAME', 'UPGRADE'], value_vars=['DURATION', 'REQUEST_TO_BEGIN'], var_name='Metric', value_name='Value')

# Create side-by-side box plots for durations
fig = px.box(df_melted[df_melted['Metric'] == 'DURATION'], x='PRCSNAME', y='Value', color='UPGRADE',
             title='Job Duration Comparison Pre and Post-Upgrade',
             labels={'Value': 'Duration (seconds)'})

# Update layout for better readability
fig.update_layout(
    xaxis_title='Job Name',
    yaxis_title='Duration (seconds)',
    boxmode='group',  # Grouped box plots
    height=600,
    width=1200
)

fig.show()

# Create side-by-side box plots for request to begin times
fig2 = px.box(df_melted[df_melted['Metric'] == 'REQUEST_TO_BEGIN'], x='PRCSNAME', y='Value', color='UPGRADE',
              title='Request to Begin Time Comparison Pre and Post-Upgrade',
              labels={'Value': 'Request to Begin Time (seconds)'})

# Update layout for better readability
fig2.update_layout(
    xaxis_title='Job Name',
    yaxis_title='Request to Begin Time (seconds)',
    boxmode='group',  # Grouped box plots
    height=600,
    width=1200
)

fig2.show()


In [19]:
import pandas as pd
import numpy as np
import plotly.express as px

# Generating synthetic data (if not already done)
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations and request to begin time
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate average pre and post-upgrade times for each job
pre_upgrade = df[df['UPGRADE'] == False].groupby('PRCSNAME')['DURATION'].mean().reset_index()
post_upgrade = df[df['UPGRADE'] == True].groupby('PRCSNAME')['DURATION'].mean().reset_index()

# Merge pre and post-upgrade data
comparison = pd.merge(pre_upgrade, post_upgrade, on='PRCSNAME', suffixes=('_Pre', '_Post'))
comparison['Difference (minutes)'] = comparison['DURATION_Post'] - comparison['DURATION_Pre']
comparison['Improvement (%)'] = (comparison['Difference (minutes)'] / comparison['DURATION_Pre']) * -100

# Add a column for coloring the scatter plot
comparison['Change'] = comparison['Difference (minutes)'].apply(lambda x: 'Improvement' if x < 0 else 'Regression' if x > 0 else 'No Change')

# Create scatter plot
fig = px.scatter(comparison, x='DURATION_Pre', y='DURATION_Post', color='Change',
                 title='Job Completion Times Pre vs. Post Upgrade',
                 labels={'DURATION_Pre': 'Pre-Upgrade Time (minutes)', 'DURATION_Post': 'Post-Upgrade Time (minutes)'},
                 hover_data=['PRCSNAME', 'Difference (minutes)', 'Improvement (%)'])

# Add line of equality (y=x) to show no change
fig.add_shape(
    type='line',
    line=dict(dash='dash'),
    x0=0, y0=0,
    x1=comparison['DURATION_Pre'].max(),
    y1=comparison['DURATION_Pre'].max()
)

# Show plot
fig.show()


In [20]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Generating synthetic data (if not already done)
np.random.seed(42)  # For reproducibility
n_samples = 5000
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std']).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std']).reset_index()

# Merge pre and post upgrade stats
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Min', 'Pre-Upgrade Mean', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Min', 'Post-Upgrade Mean', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std']

comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME')

# Create candlestick plot
fig = go.Figure()

# Add traces for each job
for _, row in comparison.iterrows():
    fig.add_trace(go.Candlestick(
        x=[row['PRCSNAME']],
        open=[row['Pre-Upgrade Min']],
        high=[row['Pre-Upgrade Max']],
        low=[row['Pre-Upgrade Min']],
        close=[row['Pre-Upgrade Median']],
        increasing_line_color='green',
        decreasing_line_color='green',
        name=f"Pre-Upgrade {row['PRCSNAME']}",
        showlegend=True
    ))
    fig.add_trace(go.Candlestick(
        x=[row['PRCSNAME']],
        open=[row['Post-Upgrade Min']],
        high=[row['Post-Upgrade Max']],
        low=[row['Post-Upgrade Min']],
        close=[row['Post-Upgrade Median']],
        increasing_line_color='red',
        decreasing_line_color='red',
        name=f"Post-Upgrade {row['PRCSNAME']}",
        showlegend=True
    ))

# Update layout
fig.update_layout(
    title='Job Duration Statistics Pre vs. Post Upgrade',
    xaxis_title='Job Name',
    yaxis_title='Duration (minutes)',
    xaxis={'categoryorder':'total descending'},
    showlegend=False
)

# Show plot
fig.show()


In [24]:
import pandas as pd
import numpy as np
import plotly.express as px

# Generate synthetic data (if not already done)
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Melt the data for Plotly Express
df_melted = df.melt(id_vars=['PRCSNAME', 'UPGRADE'], value_vars=['DURATION'], var_name='Metric', value_name='Value')

# Create side-by-side box plots for durations
fig = px.box(df_melted, x='Value', y='PRCSNAME', color='UPGRADE',
             title='Job Duration Statistics Pre vs. Post Upgrade',
             labels={'Value': 'Duration (minutes)', 'PRCSNAME': 'Job Name'},
             points="all",  # Shows all points in the distribution
             category_orders={"PRCSNAME": df.groupby("PRCSNAME")["DURATION"].mean().sort_values().index})

# Update layout for better readability
fig.update_layout(
    xaxis_title='Duration (minutes)',
    yaxis_title='Job Name',
    height=8000  # Adjust the height for better readability
)

fig.show()


In [25]:
# Sort by the mean pre-upgrade duration (descending)
comparison = comparison.sort_values(by='Pre-Upgrade Mean', ascending=False)

# Top N jobs (adjust as needed)
top_n = 20
comparison = comparison.head(top_n)

# Plotly figure
fig = go.Figure()

# Pre-Upgrade "Candlesticks"
fig.add_trace(go.Scatter(
    x=comparison['Pre-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        symmetric=False,
        array=comparison['Pre-Upgrade Mean'] - comparison['Pre-Upgrade Min'],
        arrayminus=comparison['Pre-Upgrade Max'] - comparison['Pre-Upgrade Mean']
    ),
    name='Pre-Upgrade',
    marker=dict(color='blue')
))

# Post-Upgrade "Candlesticks"
fig.add_trace(go.Scatter(
    x=comparison['Post-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        symmetric=False,
        array=comparison['Post-Upgrade Mean'] - comparison['Post-Upgrade Min'],
        arrayminus=comparison['Post-Upgrade Max'] - comparison['Post-Upgrade Mean']
    ),
    name='Post-Upgrade',
    marker=dict(color='green')
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade (Top 20 Jobs)',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=800,
    width=1200
)
fig.update_traces(marker=dict(size=12))

fig.show()


In [26]:
# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std']).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std']).reset_index()

# Merge pre and post upgrade stats
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Min', 'Pre-Upgrade Mean', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Min', 'Post-Upgrade Mean', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std']

comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME')

# Sort by the mean pre-upgrade duration (descending)
comparison = comparison.sort_values(by='Pre-Upgrade Mean', ascending=False)

# Top N jobs (adjust as needed)
top_n = 20
comparison = comparison.head(top_n)

# Plotly figure
fig = go.Figure()

# Pre-Upgrade "Candlesticks"
fig.add_trace(go.Scatter(
    x=comparison['Pre-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        symmetric=False,
        array=comparison['Pre-Upgrade Mean'] - comparison['Pre-Upgrade Min'],
        arrayminus=comparison['Pre-Upgrade Max'] - comparison['Pre-Upgrade Mean']
    ),
    name='Pre-Upgrade',
    marker=dict(color='blue')
))

# Post-Upgrade "Candlesticks"
fig.add_trace(go.Scatter(
    x=comparison['Post-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        symmetric=False,
        array=comparison['Post-Upgrade Mean'] - comparison['Post-Upgrade Min'],
        arrayminus=comparison['Post-Upgrade Max'] - comparison['Post-Upgrade Mean']
    ),
    name='Post-Upgrade',
    marker=dict(color='green')
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade (Top 20 Jobs)',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=800,
    width=1200
)
fig.update_traces(marker=dict(size=12))

fig.show()

In [31]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Generating synthetic data (if not already done)
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std', 'count']).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std', 'count']).reset_index()

# Merge pre and post upgrade stats
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Min', 'Pre-Upgrade Mean', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std', 'Pre-Upgrade Count']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Min', 'Post-Upgrade Mean', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std', 'Post-Upgrade Count']

comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME')

# Calculate additional metrics for hover data
comparison['Difference (minutes)'] = comparison['Post-Upgrade Mean'] - comparison['Pre-Upgrade Mean']
comparison['Improvement (%)'] = (comparison['Difference (minutes)'] / comparison['Pre-Upgrade Mean']) * -100

# Sort by the largest delta between pre and post-upgrade durations
comparison = comparison.sort_values(by='Difference (minutes)', ascending=False)

# Plotly figure
fig = go.Figure()

# Pre-Upgrade "Candlesticks"
fig.add_trace(go.Scatter(
    x=comparison['Pre-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        symmetric=False,
        array=comparison['Pre-Upgrade Max'] - comparison['Pre-Upgrade Mean'],
        arrayminus=comparison['Pre-Upgrade Mean'] - comparison['Pre-Upgrade Min']
    ),
    name='Pre-Upgrade',
    marker=dict(color='blue'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Pre-Upgrade Min: %{customdata[0]:.2f}<br>"
        "Pre-Upgrade Mean: %{x:.2f}<br>"
        "Pre-Upgrade Median: %{customdata[1]:.2f}<br>"
        "Pre-Upgrade Max: %{customdata[2]:.2f}<br>"
        "Pre-Upgrade Std: %{customdata[3]:.2f}<br>"
        "Pre-Upgrade Count: %{customdata[4]}<br>"
    ),
    customdata=comparison[['Pre-Upgrade Min', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std', 'Pre-Upgrade Count']]
))

# Post-Upgrade "Candlesticks"
fig.add_trace(go.Scatter(
    x=comparison['Post-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        symmetric=False,
        array=comparison['Post-Upgrade Max'] - comparison['Post-Upgrade Mean'],
        arrayminus=comparison['Post-Upgrade Mean'] - comparison['Post-Upgrade Min']
    ),
    name='Post-Upgrade',
    marker=dict(color='green'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Post-Upgrade Min: %{customdata[0]:.2f}<br>"
        "Post-Upgrade Mean: %{x:.2f}<br>"
        "Post-Upgrade Median: %{customdata[1]:.2f}<br>"
        "Post-Upgrade Max: %{customdata[2]:.2f}<br>"
        "Post-Upgrade Std: %{customdata[3]:.2f}<br>"
        "Post-Upgrade Count: %{customdata[4]}<br>"
        "Difference (minutes): %{customdata[5]:.2f}<br>"
        "Improvement (%): %{customdata[6]:.2f}%<br>"
    ),
    customdata=comparison[['Post-Upgrade Min', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std', 'Post-Upgrade Count', 'Difference (minutes)', 'Improvement (%)']]
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=3000,  # Adjust the height for better readability with more jobs
    width=1200
)
fig.update_traces(marker=dict(size=12))

fig.show()


In [43]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Generating synthetic data (if not already done)
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

import pandas as pd
import numpy as np
import plotly.graph_objects as go

# ... (your existing code for data generation remains the same) ...

# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate statistics pre and post upgrade (no grouping to get overall stats)
stats_pre = df[df['UPGRADE'] == False]['DURATION'].agg(['min', 'mean', 'median', 'max', 'std'])
stats_post = df[df['UPGRADE'] == True]['DURATION'].agg(['min', 'mean', 'median', 'max', 'std'])

# Create a summary DataFrame for the overall statistics
summary_data = {
    'Category': ['Pre-Upgrade', 'Post-Upgrade'],
    'Min': [stats_pre['min'], stats_post['min']],
    'Mean': [stats_pre['mean'], stats_post['mean']],
    'Median': [stats_pre['median'], stats_post['median']],
    'Max': [stats_pre['max'], stats_post['max']],
    'Std': [stats_pre['std'], stats_post['std']]
}

df_summary = pd.DataFrame(summary_data)

# Calculate statistics per job
stats_pre_per_job = df[df['UPGRADE'] == False].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std']).reset_index()
stats_post_per_job = df[df['UPGRADE'] == True].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std']).reset_index()

# Merge pre and post upgrade stats
stats_pre_per_job.columns = ['PRCSNAME', 'Pre-Upgrade Min', 'Pre-Upgrade Mean', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std']
stats_post_per_job.columns = ['PRCSNAME', 'Post-Upgrade Min', 'Post-Upgrade Mean', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std']

comparison = pd.merge(stats_pre_per_job, stats_post_per_job, on='PRCSNAME')

# Calculate the difference in means
comparison['Mean Difference'] = comparison['Post-Upgrade Mean'] - comparison['Pre-Upgrade Mean']
comparison['Relative Difference (%)'] = (comparison['Mean Difference'] / comparison['Pre-Upgrade Mean']) * 100

# Sort by the absolute difference (descending) to prioritize both increases and decreases
comparison['Abs Mean Difference'] = comparison['Mean Difference'].abs()
comparison.sort_values(by='Abs Mean Difference', ascending=False, inplace=True)


# Create traces for the overall summary
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=df_summary['Mean'],
    y=df_summary['Category'],
    mode='markers',
    error_x=dict(type='data', array=df_summary['Std']),
    name='Overall',
    marker=dict(color='black', size=12),
    hovertemplate="%{y}:<br>" +
                  "Mean: %{x:.2f} mins<br>" +
                  "Min/Max: %{customdata[0]:.2f} / %{customdata[1]:.2f} mins<br>" +
                  "Std: %{customdata[2]:.2f} mins",
    customdata=df_summary[['Min', 'Max', 'Std']]
))

# Create traces for individual jobs (same as before, but for all jobs)
fig.add_trace(go.Scatter(
    x=comparison['Pre-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        symmetric=False,
        array=comparison['Pre-Upgrade Max'] - comparison['Pre-Upgrade Mean'],
        arrayminus=comparison['Pre-Upgrade Mean'] - comparison['Pre-Upgrade Min']
    ),
    name='Pre-Upgrade',
    marker=dict(color='blue'),
    hovertemplate=(
        "Job: %{y}<br>" +
        "Pre-Upgrade Mean: %{x:.2f} mins<br>" +
        "Pre-Upgrade Min/Max: %{customdata[0]:.2f} / %{customdata[1]:.2f} mins<br>" +
        "Pre-Upgrade Std: %{customdata[2]:.2f} mins"
    ),
    customdata=comparison[['Pre-Upgrade Min', 'Pre-Upgrade Max', 'Pre-Upgrade Std']]
))


# Post-Upgrade "Candlesticks" (for all jobs)
fig.add_trace(go.Scatter(
    x=comparison['Post-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        symmetric=False,
        array=comparison['Post-Upgrade Max'] - comparison['Post-Upgrade Mean'],
        arrayminus=comparison['Post-Upgrade Mean'] - comparison['Post-Upgrade Min']
    ),
    name='Post-Upgrade',
    marker=dict(color='green'),
    hovertemplate=(
        "Job: %{y}<br>" +
        "Post-Upgrade Mean: %{x:.2f} mins<br>" +
        "Post-Upgrade Min/Max: %{customdata[0]:.2f} / %{customdata[1]:.2f} mins<br>" +
        "Post-Upgrade Std: %{customdata[2]:.2f} mins<br>" +
        "Mean Difference: %{customdata[3]:+.2f} mins<br>" +  # Display change in mean
        "Relative Difference: %{customdata[4]:+.2f}%"       # Display percentage change
    ),
    customdata=comparison[['Post-Upgrade Min', 'Post-Upgrade Max', 'Post-Upgrade Std', 'Mean Difference', 'Relative Difference (%)']]
))

# Figure layout
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade (All Jobs)',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=3000,  
    width=1200,
    yaxis={'categoryorder': 'array', 'categoryarray': comparison['PRCSNAME']}
)

fig.show()


In [49]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Generating synthetic data (if not already done)
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std', 'count']).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std', 'count']).reset_index()

# Merge pre and post upgrade stats
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Min', 'Pre-Upgrade Mean', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std', 'Pre-Upgrade Count']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Min', 'Post-Upgrade Mean', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std', 'Post-Upgrade Count']

comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME')

# Calculate additional metrics for hover data
comparison['Difference (minutes)'] = comparison['Post-Upgrade Mean'] - comparison['Pre-Upgrade Mean']
comparison['Improvement (%)'] = (comparison['Difference (minutes)'] / comparison['Pre-Upgrade Mean']) * -100

# Sort by the largest increase in post-upgrade duration
comparison = comparison.sort_values(by='Difference (minutes)', ascending=False)

# Plotly figure
fig = go.Figure()

# Pre-Upgrade durations
fig.add_trace(go.Bar(
    x=comparison['Pre-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    orientation='h',
    name='Pre-Upgrade',
    marker=dict(color='blue'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Pre-Upgrade Min: %{customdata[0]:.2f}<br>"
        "Pre-Upgrade Mean: %{x:.2f}<br>"
        "Pre-Upgrade Median: %{customdata[1]:.2f}<br>"
        "Pre-Upgrade Max: %{customdata[2]:.2f}<br>"
        "Pre-Upgrade Std: %{customdata[3]:.2f}<br>"
        "Pre-Upgrade Count: %{customdata[4]}<br>"
    ),
    customdata=comparison[['Pre-Upgrade Min', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std', 'Pre-Upgrade Count']]
))

# Post-Upgrade durations
fig.add_trace(go.Bar(
    x=comparison['Post-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    orientation='h',
    name='Post-Upgrade',
    marker=dict(color='green'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Post-Upgrade Min: %{customdata[0]:.2f}<br>"
        "Post-Upgrade Mean: %{x:.2f}<br>"
        "Post-Upgrade Median: %{customdata[1]:.2f}<br>"
        "Post-Upgrade Max: %{customdata[2]:.2f}<br>"
        "Post-Upgrade Std: %{customdata[3]:.2f}<br>"
        "Post-Upgrade Count: %{customdata[4]}<br>"
        "Difference (minutes): %{customdata[5]:.2f}<br>"
        "Improvement (%): %{customdata[6]:.2f}%<br>"
    ),
    customdata=comparison[['Post-Upgrade Min', 'Post-Upgrade Mean', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std', 'Post-Upgrade Count', 'Difference (minutes)', 'Improvement (%)']]
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=3000,  # Adjust the height for better readability with more jobs
    width=1200,
    barmode='group',
    legend=dict(title='Duration'),
    hovermode='y unified'
)

fig.show()


In [51]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Generating synthetic data (if not already done)
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60  # Convert to minutes
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Create separate dataframes for pre and post-upgrade
df_pre = df[df['UPGRADE'] == False]
df_post = df[df['UPGRADE'] == True]

# Plotly figure
fig = go.Figure()

# Pre-Upgrade Box Plot
fig.add_trace(go.Box(
    x=df_pre['DURATION'],
    y=df_pre['PRCSNAME'],
    name='Pre-Upgrade',
    marker=dict(color='blue'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Duration: %{x:.2f} minutes"
    )
))

# Post-Upgrade Box Plot
fig.add_trace(go.Box(
    x=df_post['DURATION'],
    y=df_post['PRCSNAME'],
    name='Post-Upgrade',
    marker=dict(color='green'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Duration: %{x:.2f} minutes"
    )
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=3000,  # Adjust the height for better readability with more jobs
    width=1200,
    boxmode='group',
    legend=dict(title='Duration'),
    hovermode='y unified'
)

fig.show()


In [52]:
import plotly.express as px

# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME')['DURATION'].agg(['mean', 'std']).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME')['DURATION'].agg(['mean', 'std']).reset_index()

# Merge pre and post upgrade stats
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Mean', 'Pre-Upgrade Std']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Mean', 'Post-Upgrade Std']

comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME')

# Plotly figure
fig = go.Figure()

# Pre-Upgrade Mean and Std Error Bars
fig.add_trace(go.Scatter(
    x=comparison['Pre-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        array=comparison['Pre-Upgrade Std'],
        visible=True
    ),
    marker=dict(color='blue', symbol='circle'),
    name='Pre-Upgrade Mean and Std',
    hovertemplate=(
        "Job: %{y}<br>"
        "Pre-Upgrade Mean: %{x:.2f} minutes<br>"
        "Pre-Upgrade Std: %{customdata[0]:.2f} minutes"
    ),
    customdata=comparison[['Pre-Upgrade Std']]
))

# Post-Upgrade Mean and Std Error Bars
fig.add_trace(go.Scatter(
    x=comparison['Post-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        array=comparison['Post-Upgrade Std'],
        visible=True
    ),
    marker=dict(color='green', symbol='circle'),
    name='Post-Upgrade Mean and Std',
    hovertemplate=(
        "Job: %{y}<br>"
        "Post-Upgrade Mean: %{x:.2f} minutes<br>"
        "Post-Upgrade Std: %{customdata[0]:.2f} minutes"
    ),
    customdata=comparison[['Post-Upgrade Std']]
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=3000,  # Adjust the height for better readability with more jobs
    width=1200,
    legend=dict(title='Duration'),
    hovermode='y unified'
)

fig.show()


In [53]:
# Plotly figure
fig = go.Figure()

# Pre-Upgrade Violin Plot
fig.add_trace(go.Violin(
    x=df_pre['DURATION'],
    y=df_pre['PRCSNAME'],
    name='Pre-Upgrade',
    box_visible=True,
    meanline_visible=True,
    marker=dict(color='blue'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Duration: %{x:.2f} minutes"
    )
))

# Post-Upgrade Violin Plot
fig.add_trace(go.Violin(
    x=df_post['DURATION'],
    y=df_post['PRCSNAME'],
    name='Post-Upgrade',
    box_visible=True,
    meanline_visible=True,
    marker=dict(color='green'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Duration: %{x:.2f} minutes"
    )
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=3000,  # Adjust the height for better readability with more jobs
    width=1200,
    violinmode='group',
    legend=dict(title='Duration'),
    hovermode='y unified'
)

fig.show()


In [55]:
# Calculate statistics pre and post upgrade
stats_pre = df[df['UPGRADE'] == False].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std']).reset_index()
stats_post = df[df['UPGRADE'] == True].groupby('PRCSNAME')['DURATION'].agg(['min', 'mean', 'median', 'max', 'std']).reset_index()

# Merge pre and post upgrade stats
stats_pre.columns = ['PRCSNAME', 'Pre-Upgrade Min', 'Pre-Upgrade Mean', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std']
stats_post.columns = ['PRCSNAME', 'Post-Upgrade Min', 'Post-Upgrade Mean', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std']

comparison = pd.merge(stats_pre, stats_post, on='PRCSNAME')

# Plotly figure
fig = go.Figure()

# Pre-Upgrade Box Plot
fig.add_trace(go.Box(
    x=comparison['Pre-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    name='Pre-Upgrade',
    boxmean='sd',  # Shows the mean and standard deviation
    marker=dict(color='blue'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Pre-Upgrade Min: %{customdata[0]:.2f}<br>"
        "Pre-Upgrade Mean: %{x:.2f}<br>"
        "Pre-Upgrade Median: %{customdata[1]:.2f}<br>"
        "Pre-Upgrade Max: %{customdata[2]:.2f}<br>"
        "Pre-Upgrade Std: %{customdata[3]:.2f}<br>"
    ),
    customdata=comparison[['Pre-Upgrade Min', 'Pre-Upgrade Median', 'Pre-Upgrade Max', 'Pre-Upgrade Std']]
))

# Post-Upgrade Box Plot
fig.add_trace(go.Box(
    x=comparison['Post-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    name='Post-Upgrade',
    boxmean='sd',  # Shows the mean and standard deviation
    marker=dict(color='green'),
    hovertemplate=(
        "Job: %{y}<br>"
        "Post-Upgrade Min: %{customdata[0]:.2f}<br>"
        "Post-Upgrade Mean: %{x:.2f}<br>"
        "Post-Upgrade Median: %{customdata[1]:.2f}<br>"
        "Post-Upgrade Max: %{customdata[2]:.2f}<br>"
        "Post-Upgrade Std: %{customdata[3]:.2f}<br>"
    ),
    customdata=comparison[['Post-Upgrade Min', 'Post-Upgrade Median', 'Post-Upgrade Max', 'Post-Upgrade Std']]
))

# Mean and Std Error Bars
fig.add_trace(go.Scatter(
    x=comparison['Pre-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        array=comparison['Pre-Upgrade Std'],
        visible=True
    ),
    marker=dict(color='blue', symbol='circle'),
    name='Pre-Upgrade Mean and Std',
    hoverinfo='skip'
))

fig.add_trace(go.Scatter(
    x=comparison['Post-Upgrade Mean'],
    y=comparison['PRCSNAME'],
    mode='markers',
    error_x=dict(
        type='data',
        array=comparison['Post-Upgrade Std'],
        visible=True
    ),
    marker=dict(color='green', symbol='circle'),
    name='Post-Upgrade Mean and Std',
    hoverinfo='skip'
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=3000,  # Adjust the height for better readability with more jobs
    width=1200,
    boxmode='group',
    legend=dict(title='Duration'),
    hovermode='y unified'
)

fig.show()


In [56]:
comparison

PRCSNAME  Pre-Upgrade Min  Pre-Upgrade Mean  Pre-Upgrade Median  \
0    JOB_10              5.0          8.333333                10.0   
1   JOB_102              2.0          5.750000                 6.0   
2   JOB_105              6.0          6.500000                 6.5   
3   JOB_106              2.0          5.500000                 5.5   
4   JOB_108              6.0          8.666667                 8.0   
..      ...              ...               ...                 ...   
93   JOB_93              2.0          2.500000                 2.5   
94   JOB_95              4.0          4.000000                 4.0   
95   JOB_96             10.0         10.000000                10.0   
96   JOB_98              9.0          9.000000                 9.0   
97   JOB_99             13.0         13.000000                13.0   

    Pre-Upgrade Max  Pre-Upgrade Std  Post-Upgrade Min  Post-Upgrade Mean  \
0              10.0         2.886751               7.0                9.0   
1               9.0         2.986079               2.0                5.5   
2               7.0         0.707107               1.0                1.0   
3               9.0         4.949747               8.0                8.0   
4              12.0         3.055050               6.0                7.5   
..              ...              ...               ...                ...   
93              3.0         0.707107               5.0                5.0   
94              4.0              NaN              13.0               13.0   
95             10.0              NaN               4.0                4.0   
96              9.0              NaN               5.0                5.0   
97             13.0              NaN               8.0                8.0   

    Post-Upgrade Median  Post-Upgrade Max  Post-Upgrade Std  
0                   9.0              11.0          2.828427  
1                   5.5               9.0          4.949747  
2                   1.0               1.0               NaN  
3                   8.0               8.0               NaN  
4                   7.5               9.0          2.121320  
..                  ...               ...               ...  
93                  5.0               5.0               NaN  
94                 13.0              13.0               NaN  
95                  4.0               4.0               NaN  
96                  5.0               5.0               NaN  
97                  8.0               8.0               NaN  

[98 rows x 11 columns]

In [57]:
df.head()

RQSTDTTM                     BEGINDTTM  \
0 2024-05-01 00:00:00.000000000 2024-05-01 00:03:00.000000000   
1 2024-05-01 01:20:57.831325301 2024-05-01 01:24:57.831325301   
2 2024-05-01 02:41:55.662650602 2024-05-01 02:42:55.662650602   
3 2024-05-01 04:02:53.493975903 2024-05-01 04:05:53.493975903   
4 2024-05-01 05:23:51.325301204 2024-05-01 05:26:51.325301204   

                        ENDDTTM  SECONDS  MINUTES PRCSNAME RUNSTATUSDESC  \
0 2024-05-01 00:09:00.000000000       54        4  JOB_130       Success   
1 2024-05-01 01:31:57.831325301       97        3   JOB_70       Success   
2 2024-05-01 02:46:55.662650602       96        1  JOB_145       Success   
3 2024-05-01 04:09:53.493975903      262        4  JOB_123         Error   
4 2024-05-01 05:29:51.325301204      138        2   JOB_89       Success   

   PRCSINSTANCE      OPRID          RUNCNTLID  DURATION  UPGRADE  
0        971868  ewilliams  INTERNAL_PAYMENTS       6.0    False  
1        851496   bjohnson  EXTERNAL_PAYMENTS       7.0    False  
2        146403    mcurtis  INTERNAL_PAYMENTS       4.0    False  
3        715458    mcurtis  INTERNAL_PAYMENTS       4.0    False  
4        895600   bjohnson  EXTERNAL_PAYMENTS       3.0    False

In [63]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Generate synthetic data
np.random.seed(42)
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')

# Create separate dataframes for pre and post-upgrade
df_pre = df[df['UPGRADE'] == False]
df_post = df[df['UPGRADE'] == True]

# Plotly figure
fig = go.Figure()

# Pre-Upgrade Box Plot
fig.add_trace(go.Box(
    x=df_pre['DURATION'],
    y=df_pre['PRCSNAME'],
    name='Pre-Upgrade',
    marker=dict(color='blue'),
    hovertemplate="Job: %{y}<br>Duration: %{x:.2f} minutes"
))

# Post-Upgrade Box Plot
fig.add_trace(go.Box(
    x=df_post['DURATION'],
    y=df_post['PRCSNAME'],
    name='Post-Upgrade',
    marker=dict(color='green'),
    hovertemplate="Job: %{y}<br>Duration: %{x:.2f} minutes"
))

# Figure layout and customizations
fig.update_layout(
    title='Job Duration Statistics: Pre-Upgrade vs. Post-Upgrade',
    xaxis_title='Duration (Minutes)',
    yaxis_title='Job Name',
    height=3000,  # Adjust the height for better readability with more jobs
    width=1200,
    boxmode='group',
    legend=dict(title='Duration'),
    hovermode='y unified'
)

fig.show()


In [66]:
import plotly.express as px

# Filter jobs with sufficient data
valid_jobs = df_pre['PRCSNAME'].value_counts()[df_pre['PRCSNAME'].value_counts() >= 2].index
valid_jobs = valid_jobs.intersection(df_post['PRCSNAME'].value_counts()[df_post['PRCSNAME'].value_counts() >= 2].index)

# Select top jobs for demonstration (e.g., top 5)
top_jobs = valid_jobs[:50]

# Melt data for easier plotting
df_long = df[df['PRCSNAME'].isin(top_jobs)].copy()
df_long['Upgrade'] = np.where(df_long['UPGRADE'], 'Post-Upgrade', 'Pre-Upgrade')

# Plotly figure
fig = px.violin(df_long, x='DURATION', y='PRCSNAME', color='Upgrade', box=True, points="all",
                category_orders={"PRCSNAME": top_jobs},
                title='Violin Plots of Job Durations Before and After Upgrade',
                labels={"DURATION": "Job Duration (Minutes)", "PRCSNAME": "Job Name", "Upgrade": "Upgrade Status"})

fig.update_layout(height=1000, width=1200)

fig.show()


In [68]:
import pandas as pd
import numpy as np
import plotly.figure_factory as ff
import plotly.subplots as sp
import plotly.graph_objects as go

# Generate synthetic data (if not already done)
np.random.seed(42)  # For reproducibility
n_samples = 500
dates_before = pd.date_range(start='2024-05-01', end='2024-05-15', periods=n_samples//2)
dates_after = pd.date_range(start='2024-06-01', end='2024-06-15', periods=n_samples//2)
dates = np.concatenate([dates_before, dates_after])

data = {
    'RQSTDTTM': dates,
    'BEGINDTTM': dates + pd.to_timedelta(np.random.randint(1, 5, n_samples), unit='m'),
    'ENDDTTM': dates + pd.to_timedelta(np.random.randint(5, 15, n_samples), unit='m'),
    'SECONDS': np.random.randint(30, 300, n_samples),
    'MINUTES': np.random.randint(1, 5, n_samples),
    'PRCSNAME': np.random.choice([f'JOB_{i}' for i in range(1, 167)], n_samples),
    'RUNSTATUSDESC': np.random.choice(['Success', 'Error'], n_samples, p=[0.9, 0.1]),
    'PRCSINSTANCE': np.random.randint(100000, 999999, n_samples),
    'OPRID': np.random.choice(['mcurtis', 'jdoe', 'asmith', 'bjohnson', 'ewilliams'], n_samples),
    'RUNCNTLID': np.random.choice(['EXTERNAL_PAYMENTS', 'INTERNAL_PAYMENTS'], n_samples)
}

df = pd.DataFrame(data)

# Calculate durations
df['DURATION'] = (df['ENDDTTM'] - df['BEGINDTTM']).dt.total_seconds() / 60
df['UPGRADE'] = df['RQSTDTTM'] >= pd.Timestamp('2024-06-01')
df['Upgrade'] = np.where(df['UPGRADE'], 'Post-Upgrade', 'Pre-Upgrade')

# Filter jobs with sufficient data
valid_jobs = df['PRCSNAME'].value_counts()[df['PRCSNAME'].value_counts() >= 2].index

# Select a subset of jobs for the plot (e.g., top 10 jobs by frequency)
top_jobs = valid_jobs[:10]
df_top = df[df['PRCSNAME'].isin(top_jobs)]

# Initialize subplots
fig = sp.make_subplots(rows=len(top_jobs), cols=1, subplot_titles=top_jobs, vertical_spacing=0.1)

# Create KDE plots for each job
for i, job in enumerate(top_jobs):
    job_pre = df_top[(df_top['PRCSNAME'] == job) & (df_top['Upgrade'] == 'Pre-Upgrade')]['DURATION']
    job_post = df_top[(df_top['PRCSNAME'] == job) & (df_top['Upgrade'] == 'Post-Upgrade')]['DURATION']
    
    hist_data = [job_pre, job_post]
    group_labels = ['Pre-Upgrade', 'Post-Upgrade']
    
    kde_fig = ff.create_distplot(hist_data, group_labels, show_hist=False, show_rug=False)
    
    for trace in kde_fig['data']:
        fig.add_trace(trace, row=i+1, col=1)

# Update layout
fig.update_layout(
    height=2000,  # Adjust the height based on the number of jobs
    width=1000,
    title_text='KDE Plots of Job Durations Before and After Upgrade',
    showlegend=True
)

fig.show()



ValueError: `dataset` input should have multiple elements.